In [1]:
from requests import request
from requests.compat import *
from bs4 import BeautifulSoup
import pandas as pd
import math
import time

def makePageDF(category_id, page_id, pagingsize):
    url = 'https://search.shopping.naver.com/search/category/' + str(category_id)
    params = {
        'pagingIndex' : str(page_id),
        'pagingSize' : str(pagingsize),
        'productSet' : 'model'
    }
    headers = {'User-Agent': 'Yeti',}
    resp = request('GET',url=url, params=params, headers=headers)
    print(resp.request.url)
    dom = BeautifulSoup(resp.text, 'html.parser')
    script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
    data = json.loads(script_tag.text)
    itemList = data['props']['pageProps']['initialState']['products']
    
    
    # 각 상품의 정보를 저장할 리스트를 생성합니다.
    products_info = []

    for item in itemList['list'][:pagingsize]:

        attributes_dict = dict()
        # 'attributeValue'와 'characterValue' 문자열을 리스트로 분리합니다.
        attribute_values = item['item'].get('attributeValue','').split('|')
        character_values = item['item'].get('characterValue','').split('|')

        # 'attributeValue' 리스트의 각 요소에서 '_M' 문자열을 제거합니다.
        attribute_values = [value.replace('_M', '') for value in attribute_values]

        min_len = min(len(attribute_values), len(character_values))

        for j in range(min_len):
            attribute = attribute_values[j]
            character = character_values[j]

            if attribute in attributes_dict:
                attributes_dict[attribute].append(character)
            else:
                attributes_dict[attribute] = [character]

        attribute_list = [item['item']['category3Name']]

        for i in attributes_dict:
            if i not in ['용량', '구성', '']:
                attribute_list = attribute_list + attributes_dict[i]
            else:
                continue

        dict_data = {
            'ID': item['item']['id'],
            '상품명': item['item']['productName'],
            '상품 카테고리 대분류': item['item']['category1Name'],
            '상품 카테고리 중분류': item['item']['category2Name'],
            '상품 카테고리 소분류': item['item']['category3Name'],
            '제조사': item['item'].get('maker',''),
            '브랜드': item['item'].get('brand',''),
            '특징': attribute_list,
            '느낌': item['item'].get('atmtTag','').replace('|',',').split(','),
            '평점': item['item'].get('scoreInfo',0),
        }

        products_info.append(dict_data)

    total = data['props']['pageProps']['initialState']['products']['total']
    total_page = math.ceil(total/int(params['pagingSize']))
        
        # 딕셔너리의 리스트를 데이터프레임으로 변환합니다.
    df = pd.DataFrame(products_info)
    
    return df,total_page

In [2]:
def CrawlCategoryId(category_id, filename='categoryId.csv'):
    url = 'https://search.shopping.naver.com/search/category/'
    headers = {'User-Agent': 'Yeti',}
    params = {
        'pagingIndex' : '1',
        'pagingSize' : '80',
        'productSet' : 'model'
    }
    resp = request('GET',url=url+str(category_id), headers=headers)
    print(resp.request.url)

    dom = BeautifulSoup(resp.text, 'html.parser')
    script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
    data = json.loads(script_tag.text)

    title_value_pairs = [{'title': x['title'], 'value': x['value']} for x in data['props']['pageProps']['initialState']['mainFilters'][0]['filterValues']]
    category_df = pd.DataFrame(title_value_pairs)

    rows_to_drop = []
    rows_to_append = []

    for index, row in category_df.iterrows():
        category_url = url + str(row['value'])
        time.sleep(0.3)
        resp = request('GET',url=category_url,params=params, headers=headers)
        print(resp.request.url)
        dom = BeautifulSoup(resp.text, 'html.parser')
        script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
        data = json.loads(script_tag.text)

        if data['props']['pageProps']['initialState']['subFilters']:
            product_count = data['props']['pageProps']['initialState']['subFilters'][0]['filterValues'][1]['productCount']
        else:
            product_count = 0

        if int(product_count)/int(params['pagingSize']) > 100:
            print(row['title'], row['value'], product_count, product_count/int(params['pagingSize']))
            rows_to_drop.append(index)
            sub_title_value_pairs = [{'title': x['title'], 'value': x['value']} for x in data['props']['pageProps']['initialState']['mainFilters'][0]['filterValues']]
            rows_to_append += sub_title_value_pairs

    # Drop the rows from original DataFrame
    category_df = category_df.drop(rows_to_drop)

    # Append new rows to DataFrame
    category_df = category_df.append(rows_to_append, ignore_index=True)

    category_df.to_csv(filename, index=False, encoding='utf-8-sig')

    return list(category_df['value'])

In [3]:
def makeCategoryDF(category_id):

    category_id_list = CrawlCategoryId(category_id)
    dfs = []  # 데이터프레임을 저장할 리스트를 생성합니다.

    for k in category_id_list:
        new_df,total_page = makePageDF(k,1,80)
        dfs.append(new_df)  # 데이터프레임을 리스트에 추가합니다.
        if total_page > 1:
            for i in range(2,total_page+1):
                new_df, _ = makePageDF(k,i,80)
                time.sleep(0.3)
                dfs.append(new_df)  # 데이터프레임을 리스트에 추가합니다.

    # 모든 페이지를 처리한 후에 각 데이터프레임을 별도의 파일로 저장합니다.
    for i, df in enumerate(dfs):
        df.to_csv(str(category_id)+f'/temp_df_{i}.csv',index=False)

    # 각 파일을 불러와서 중복을 제거합니다.
    unique_ids = set()
    for i in range(len(dfs)):
        df = pd.read_csv(str(category_id)+f'/temp_df_{i}.csv')
        df = df[~df['ID'].isin(unique_ids)]
        unique_ids.update(df['ID'])
        df.to_csv(str(category_id)+f'/temp_df_{i}.csv',index=False)

    # 중복이 제거된 데이터프레임을 다시 불러와서 하나의 데이터프레임으로 합칩니다.
    df = pd.concat([pd.read_csv(str(category_id)+f'/temp_df_{i}.csv') for i in range(len(dfs))], ignore_index=True)

    df = df.drop_duplicates(subset=['ID'])
    df = df.drop_duplicates(subset=['상품명','제조사'])
    df = df.drop_duplicates(subset=['상품명','브랜드'], ignore_index=True)

    df = pd.DataFrame(df).astype({'제조사': 'category'})
    df = pd.DataFrame(df).astype({'브랜드': 'category'})

    return df

In [4]:
df = makeCategoryDF(100001011)

https://search.shopping.naver.com/search/category/100001011
https://search.shopping.naver.com/search/category/100010202?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010203?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010204?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010205?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010206?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010207?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010208?pagingIndex=1&pagingSize=80&productSet=model


C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\2615888957.py:46: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  category_df = category_df.append(rows_to_append, ignore_index=True)


https://search.shopping.naver.com/search/category/100010202?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=2&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=3&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=4&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=5&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=6&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=7&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=8&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100010202?pagingIndex=9&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/10001

In [5]:
df.to_excel('test1.xlsx')

In [24]:
def add_attribute(df,name):
    if name == '성분':
        ingredients_list = []
        for item in df['ID']:
            url = 'https://search.shopping.naver.com/catalog/' + str(item)
            headers = {'User-Agent': 'Yeti',}
            resp = request('GET',url=url,headers=headers)
            print(resp.request.url)
            dom = BeautifulSoup(resp.text, 'html.parser')
            script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
            data = json.loads(script_tag.text)

            ingredients = data['props']['pageProps']['initialState']['catalog']['cosmeticIngredient'].get('allIngredients','')
            if ingredients:
                ingredients = ingredients.replace(' ','').split(',')
            ingredients_list.append(ingredients)
            time.sleep(0.3)
        df[name] = ingredients_list
        
    elif name == '네이버 추천 상품 ID':
        recommend_item_id_list = []
        for item in df['ID']:
            url = 'https://search.shopping.naver.com/catalog/' + str(item)
            headers = {'User-Agent': 'Yeti',}
            resp = request('GET',url=url,headers=headers)
            print(resp.request.url)
            dom = BeautifulSoup(resp.text, 'html.parser')
            script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
            data = json.loads(script_tag.text)
            recommend_item = data['props']['pageProps']['initialState']['catalog']['recommend']['explore']['recItems']
            recommend_item_id = []
            for i in range(len(recommend_item)):
                if recommend_item[i]['nPayMblType'] == '0':
                    recommend_item_id.append(recommend_item[i]['nvMid'])
                else:
                    continue
            recommend_item_id_list.append(recommend_item_id)
            time.sleep(0.3)
        df[name] = recommend_item_id_list

In [37]:
def seperateDF(df, name):
    df_copy = df.copy()
    
    small_df = df_copy.explode(name)[['ID','상품명',name,'평점']]
    attributes = pd.DataFrame(small_df[name].unique()).reset_index()
    attributes.columns = [name + '_id', name]
    attributes = pd.DataFrame(attributes).astype({name + '_id': 'category'})
    attribute_list = list(attributes[name])
    merged_df = pd.merge(small_df, attributes, on=[name])

    for i in attribute_list:
        data_list = []
        for j in range(len(df)):
            if i in df_copy[name][j]:
                data_list.append(True)
            else:
                data_list.append(False)
        df_copy[i] = data_list
        
    return df_copy, attributes, merged_df

In [11]:
add_attribute(df,'성분')

https://search.shopping.naver.com/catalog/28269744554
https://search.shopping.naver.com/catalog/29502248618
https://search.shopping.naver.com/catalog/25261181522
https://search.shopping.naver.com/catalog/33208679619
https://search.shopping.naver.com/catalog/4053407990
https://search.shopping.naver.com/catalog/4139689180
https://search.shopping.naver.com/catalog/21800772051
https://search.shopping.naver.com/catalog/28727569554
https://search.shopping.naver.com/catalog/33192635618
https://search.shopping.naver.com/catalog/33490913619
https://search.shopping.naver.com/catalog/15567261535
https://search.shopping.naver.com/catalog/21478983677
https://search.shopping.naver.com/catalog/36514611620
https://search.shopping.naver.com/catalog/26979721522
https://search.shopping.naver.com/catalog/20448242803
https://search.shopping.naver.com/catalog/26525724526
https://search.shopping.naver.com/catalog/7610416204
https://search.shopping.naver.com/catalog/23268315491
https://search.shopping.naver.c

https://search.shopping.naver.com/catalog/34956546619
https://search.shopping.naver.com/catalog/35624078619
https://search.shopping.naver.com/catalog/21377457712
https://search.shopping.naver.com/catalog/41259148619
https://search.shopping.naver.com/catalog/27023486522
https://search.shopping.naver.com/catalog/22236665755
https://search.shopping.naver.com/catalog/23367000490
https://search.shopping.naver.com/catalog/34936361618
https://search.shopping.naver.com/catalog/15067746158
https://search.shopping.naver.com/catalog/25230679524
https://search.shopping.naver.com/catalog/5835741119
https://search.shopping.naver.com/catalog/23366997490
https://search.shopping.naver.com/catalog/26759270522
https://search.shopping.naver.com/catalog/29486996619
https://search.shopping.naver.com/catalog/22290276109
https://search.shopping.naver.com/catalog/28742527555
https://search.shopping.naver.com/catalog/35481308619
https://search.shopping.naver.com/catalog/5475574495
https://search.shopping.naver.

https://search.shopping.naver.com/catalog/28825678587
https://search.shopping.naver.com/catalog/24311984522
https://search.shopping.naver.com/catalog/41449137618
https://search.shopping.naver.com/catalog/28000574524
https://search.shopping.naver.com/catalog/23528341493
https://search.shopping.naver.com/catalog/32000545619
https://search.shopping.naver.com/catalog/28682551557
https://search.shopping.naver.com/catalog/34137017619
https://search.shopping.naver.com/catalog/24549598524
https://search.shopping.naver.com/catalog/21798111065
https://search.shopping.naver.com/catalog/31455844619
https://search.shopping.naver.com/catalog/17469290748
https://search.shopping.naver.com/catalog/35690169618
https://search.shopping.naver.com/catalog/31456725619
https://search.shopping.naver.com/catalog/30085666626
https://search.shopping.naver.com/catalog/5419348994
https://search.shopping.naver.com/catalog/39968438624
https://search.shopping.naver.com/catalog/30314536630
https://search.shopping.naver

https://search.shopping.naver.com/catalog/29736343619
https://search.shopping.naver.com/catalog/12323992378
https://search.shopping.naver.com/catalog/41472164622
https://search.shopping.naver.com/catalog/36469053618
https://search.shopping.naver.com/catalog/23280091491
https://search.shopping.naver.com/catalog/28000312523
https://search.shopping.naver.com/catalog/28065141522
https://search.shopping.naver.com/catalog/31417633618
https://search.shopping.naver.com/catalog/31455225622
https://search.shopping.naver.com/catalog/4141772136
https://search.shopping.naver.com/catalog/5640360099
https://search.shopping.naver.com/catalog/41448968625
https://search.shopping.naver.com/catalog/5745032465
https://search.shopping.naver.com/catalog/33039006621
https://search.shopping.naver.com/catalog/28942633586
https://search.shopping.naver.com/catalog/4113374598
https://search.shopping.naver.com/catalog/31021204619
https://search.shopping.naver.com/catalog/23809224525
https://search.shopping.naver.co

https://search.shopping.naver.com/catalog/31104252619
https://search.shopping.naver.com/catalog/30878927618
https://search.shopping.naver.com/catalog/33938588622
https://search.shopping.naver.com/catalog/14409578959
https://search.shopping.naver.com/catalog/31884026618
https://search.shopping.naver.com/catalog/37615421622
https://search.shopping.naver.com/catalog/37857646618
https://search.shopping.naver.com/catalog/29032290586
https://search.shopping.naver.com/catalog/28272114555
https://search.shopping.naver.com/catalog/32710635619
https://search.shopping.naver.com/catalog/33187088618
https://search.shopping.naver.com/catalog/28656065556
https://search.shopping.naver.com/catalog/32068193618
https://search.shopping.naver.com/catalog/26481882522
https://search.shopping.naver.com/catalog/33858957618
https://search.shopping.naver.com/catalog/29230564624
https://search.shopping.naver.com/catalog/32148367618
https://search.shopping.naver.com/catalog/12771869774
https://search.shopping.nave

...

https://search.shopping.naver.com/catalog/41732448618
https://search.shopping.naver.com/catalog/31313798624
https://search.shopping.naver.com/catalog/15266139438
https://search.shopping.naver.com/catalog/27983219522
https://search.shopping.naver.com/catalog/27984993526
https://search.shopping.naver.com/catalog/30929398619
https://search.shopping.naver.com/catalog/22127515706
https://search.shopping.naver.com/catalog/22127618026
https://search.shopping.naver.com/catalog/24513523529
https://search.shopping.naver.com/catalog/27891914522
https://search.shopping.naver.com/catalog/33425029620
https://search.shopping.naver.com/catalog/23680047496
https://search.shopping.naver.com/catalog/41139467618
https://search.shopping.naver.com/catalog/30326545618
https://search.shopping.naver.com/catalog/13419365431
https://search.shopping.naver.com/catalog/39068574618
https://search.shopping.naver.com/catalog/12968540045
https://search.shopping.naver.com/catalog/36405800618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/32803508618
https://search.shopping.naver.com/catalog/40902285618
https://search.shopping.naver.com/catalog/29148841623
https://search.shopping.naver.com/catalog/33425030620
https://search.shopping.naver.com/catalog/39022842621
https://search.shopping.naver.com/catalog/40957387619
https://search.shopping.naver.com/catalog/36332088618
https://search.shopping.naver.com/catalog/35366227618
https://search.shopping.naver.com/catalog/32086818619
https://search.shopping.naver.com/catalog/27436225532
https://search.shopping.naver.com/catalog/34925081618
https://search.shopping.naver.com/catalog/31349623618
https://search.shopping.naver.com/catalog/29325947622
https://search.shopping.naver.com/catalog/33441269621
https://search.shopping.naver.com/catalog/32068193619
https://search.shopping.naver.com/catalog/31466655618
https://search.shopping.naver.com/catalog/38288076619
https://search.shopping.naver.com/catalog/31160772618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/35707301619
https://search.shopping.naver.com/catalog/38287640618
https://search.shopping.naver.com/catalog/32456015620
https://search.shopping.naver.com/catalog/29738338621
https://search.shopping.naver.com/catalog/36332205622
https://search.shopping.naver.com/catalog/38228404618
https://search.shopping.naver.com/catalog/31041555620
https://search.shopping.naver.com/catalog/35481660618
https://search.shopping.naver.com/catalog/35725652618
https://search.shopping.naver.com/catalog/38289914618
https://search.shopping.naver.com/catalog/38361727621
https://search.shopping.naver.com/catalog/31719864619
https://search.shopping.naver.com/catalog/31232122621
https://search.shopping.naver.com/catalog/38228089619
https://search.shopping.naver.com/catalog/33363718619
https://search.shopping.naver.com/catalog/38148355620
https://search.shopping.naver.com/catalog/21515109240
https://search.shopping.naver.com/catalog/36335070618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/14798462343
https://search.shopping.naver.com/catalog/5588595342
https://search.shopping.naver.com/catalog/29696957620
https://search.shopping.naver.com/catalog/35342234623
https://search.shopping.naver.com/catalog/31552264621
https://search.shopping.naver.com/catalog/34137178619
https://search.shopping.naver.com/catalog/30787128618
https://search.shopping.naver.com/catalog/29488315619
https://search.shopping.naver.com/catalog/23198805492
https://search.shopping.naver.com/catalog/39625023621
https://search.shopping.naver.com/catalog/26599339523
https://search.shopping.naver.com/catalog/18355171195
https://search.shopping.naver.com/catalog/4133636866
https://search.shopping.naver.com/catalog/23449530491
https://search.shopping.naver.com/catalog/17770605464
https://search.shopping.naver.com/catalog/33837851619
https://search.shopping.naver.com/catalog/18026551941
https://search.shopping.naver.com/catalog/34137992618
https://search.shopping.naver.

https://search.shopping.naver.com/catalog/33426799620
https://search.shopping.naver.com/catalog/33096764623
https://search.shopping.naver.com/catalog/30254937624
https://search.shopping.naver.com/catalog/40123350618
https://search.shopping.naver.com/catalog/37736871623
https://search.shopping.naver.com/catalog/36970022618
https://search.shopping.naver.com/catalog/33117300620
https://search.shopping.naver.com/catalog/38224591620
https://search.shopping.naver.com/catalog/36538125618
https://search.shopping.naver.com/catalog/38801418619
https://search.shopping.naver.com/catalog/28302854554
https://search.shopping.naver.com/catalog/39024109618
https://search.shopping.naver.com/catalog/36538235619
https://search.shopping.naver.com/catalog/28953958592
https://search.shopping.naver.com/catalog/38380102624
https://search.shopping.naver.com/catalog/40122743621
https://search.shopping.naver.com/catalog/28302907558
https://search.shopping.naver.com/catalog/34956475622
https://search.shopping.nave

In [27]:
df.to_excel('test1.xlsx')

In [38]:
from multisage.builder import PandasGraphBuilder

attributes_df, attributes, attributes_merged_df = seperateDF(df, '특징')

# 그래프의 기본적인 노드와 엣지만 생성
graph_builder = PandasGraphBuilder()
graph_builder.add_entities(attributes, '특징_id', '특징')
graph_builder.add_entities(df, 'ID', '상품')
graph_builder.add_binary_relations(attributes_merged_df, '특징_id', 'ID', 'define')
graph_builder.add_binary_relations(attributes_merged_df, 'ID', '특징_id', 'define-by')
g = graph_builder.build()

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

...

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

In [39]:
# 그래프 구조 확인

print("Number of nodes per type:")
print(g.number_of_nodes())
print("Number of edges per type:")
print(g.number_of_edges())
print("Node types:")
print(g.ntypes)
print("Edge types:")
print(g.etypes)

# 노드 데이터 확인
for ntype in g.ntypes:
    print(f"Node type: {ntype}")
    print(g.nodes[ntype].data)

# 엣지 데이터 확인
for stype, etype, dtype in g.canonical_etypes:
    print(f"Edge type: {etype}")
    print(g.edges[etype].data)

# 그래프 구조 확인
print("Graph structure:")
print(g)

Number of nodes per type:
8057
Number of edges per type:
9060
Node types:
['상품', '특징']
Edge types:
['define-by', 'define']
Node type: 상품
{}
Node type: 특징
{}
Edge type: define-by
{}
Edge type: define
{}
Graph structure:
Graph(num_nodes={'상품': 4530, '특징': 3527},
      num_edges={('상품', 'define-by', '특징'): 4530, ('특징', 'define', '상품'): 4530},
      metagraph=[('상품', '특징', 'define-by'), ('특징', '상품', 'define')])


In [40]:
df

ID                          상품명 상품 카테고리 대분류 상품 카테고리 중분류  \
0     28269744554  검은콩 보습 진정 모닝 샴푸 로즈마리향 400ml      화장품/미용        헤어케어   
1     29502248618            어글리솝 더 님 민감성용 97g      화장품/미용        헤어케어   
2     25261181522            가려운 두피케어 샴푸 850ml      화장품/미용        헤어케어   
3     33208679619            쿨 멘솔 샴푸 850ml(신형)      화장품/미용        헤어케어   
4      4053407990              카페인 샴푸 C1 250ml      화장품/미용        헤어케어   
...           ...                          ...         ...         ...   
4525  32238886623              니욕 샴푸바 그린터치 80g      화장품/미용        헤어케어   
4526  32241470618                일랑일랑 헤어바 100g      화장품/미용        헤어케어   
4527  36623871618                캐럿히어로 샴푸바 50g      화장품/미용        헤어케어   
4528  32240713619         촌스러운 샴푸바 두피 튼튼 청 80g      화장품/미용        헤어케어   
4529  36843821623              리커버 테라피 샴푸바 80g      화장품/미용        헤어케어   

     상품 카테고리 소분류     제조사    브랜드  \
0             샴푸  동방코스메틱     올솔   
1             샴푸   프롬더랜드  프롬더랜드   
2             샴푸     P&G  헤드앤숄더   
3             샴푸     P&G  헤드앤숄더   
4             샴푸    닥터볼프    알페신   
...          ...     ...    ...   
4525          샴푸     NaN    NaN   
4526          샴푸     NaN    NaN   
4527          샴푸     NaN     맨심   
4528          샴푸     NaN  스페이스선   
4529          샴푸     NaN  그로우어스   

                                                     특징  \
0     ['샴푸', '모든두피용', '모든 모발용', '일반샴푸', '펌프형', '머릿결개...   
1     ['샴푸', '일반샴푸', '머릿결개선', '세정력', '풍부한 거품', '저자극'...   
2           ['샴푸', '일반샴푸', '펌프형', '세정력', '비듬케어', '그린향']   
3     ['샴푸', '일반샴푸', '펌프형', '세정력', '풍부한 거품', '유분제거',...   
4                         ['샴푸', '일반샴푸', '리퀴드형', '기타향']   
...                                                 ...   
4525  ['샴푸', '샴푸바', '고체형', '머릿결개선', '세정력', '풍부한 거품',...   
4526  ['샴푸', '샴푸바', '고체형', '세정력', '풍부한 거품', '상쾌함', '...   
4527                                      ['샴푸', '샴푸바']   
4528  ['샴푸', '샴푸바', '세정력', '풍부한 거품', '상쾌함', '저자극', '...   
4529                               ['샴푸', '샴푸바', '세정력']   

                                             느낌   평점  \
0                                      ['성분좋은']  4.8   
1                                          ['']  0.0   
2                     ['가려운두피', '두피가시원한', '비듬']  4.8   
3                                          ['']  4.8   
4     ['두피가시원한', '쿨링감있는', '탈모', '향좋은', '힘없는모발']  4.8   
...                                         ...  ...   
4525                                       ['']  NaN   
4526                                       ['']  NaN   
4527                                       ['']  NaN   
4528                                       ['']  NaN   
4529                                       ['']  NaN   

                                                     성분  
0     [검정콩추출물, 다이소듐라우레스설포석시네이트, 정제수, 라우릴베타인, 프로필렌글라이...  
1                                                    []  
2     [정제수, 소듐라우레스설페이트, 소듐자일렌설포네이트, 글라이콜다이스테아레이트, 코카...  
3                                                    []  
4     [리모넨, 멘톨, 비타민E, 판테놀, 시트릭애씨드, 소듐벤조에이트, 프로필파라벤, ...  
...                                                 ...  
4525                                                 []  
4526                                                 []  
4527                                                 []  
4528                                                 []  
4529  [소듐코코일이세티오네이트, 옥수수전분, 정제수, 글리세린, 해바라기씨오일, 잔탄검,...  

[4530 rows x 11 columns]

In [44]:
import torch

attributes_df, attributes, attributes_merged_df = seperateDF(df, '특징')
df['성분'] = df['성분'].fillna('[]')
ingredient_df, ingredients, ingredient_merged_df = seperateDF(df,'성분')

g.nodes['특징'].data['id'] = torch.LongTensor(attributes['특징_id'].cat.codes.values)

attribute_columns = attributes_df.columns.drop(['ID', '상품명', '상품 카테고리 대분류', '상품 카테고리 중분류','상품 카테고리 소분류','제조사','브랜드','특징','느낌','평점','성분'])
attributes_df[attribute_columns] = attributes_df[attribute_columns].fillna(False).astype('bool')
g.nodes['상품'].data['특징'] = torch.FloatTensor(attributes_df[attribute_columns].values)

attribute_columns = ingredient_df.columns.drop(['ID', '상품명', '상품 카테고리 대분류', '상품 카테고리 중분류','상품 카테고리 소분류','제조사','브랜드','특징'])
ingredient_df[attribute_columns] = ingredient_df[attribute_columns].fillna(False).astype('bool')
g.nodes['상품'].data['성분'] = torch.FloatTensor(ingredient_df[attribute_columns].values)

df['평점'] = df['평점'].fillna(0.0)
g.edges['define'].data['rating'] = torch.LongTensor(df['평점'].values)
g.edges['define-by'].data['rating'] = torch.LongTensor(df['평점'].values)


C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

...

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

In [45]:
# 그래프 구조 확인

print("Number of nodes per type:")
print(g.number_of_nodes())
print("Number of edges per type:")
print(g.number_of_edges())
print("Node types:")
print(g.ntypes)
print("Edge types:")
print(g.etypes)

# 노드 데이터 확인
for ntype in g.ntypes:
    print(f"Node type: {ntype}")
    print(g.nodes[ntype].data)

# 엣지 데이터 확인
for stype, etype, dtype in g.canonical_etypes:
    print(f"Edge type: {etype}")
    print(g.edges[etype].data)

# 그래프 구조 확인
print("Graph structure:")
print(g)

Number of nodes per type:
8057
Number of edges per type:
9060
Node types:
['상품', '특징']
Edge types:
['define-by', 'define']
Node type: 상품
{'특징': tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [0., 1., 0.,  ..., 0., 0., 0.],
        [0., 0., 1.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 1., 0.],
        [0., 0., 0.,  ..., 0., 0., 1.],
        [0., 0., 0.,  ..., 0., 0., 0.]]), '성분': tensor([[1., 1., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 1., 1.,  ..., 0., 0., 0.],
        ...,
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 1.]])}
Node type: 특징
{'id': tensor([   0,    1,    2,  ..., 3524, 3525, 3526])}
Edge type: define-by
{'rating': tensor([4, 0, 4,  ..., 0, 0, 0])}
Edge type: define
{'rating': tensor([4, 0, 4,  ..., 0, 0, 0])}
Graph structure:
Graph(num_nodes={'상품': 4530, '특징': 3527},
      num_edges={('상품', 'define-by', '특징'): 4530, ('특징', 'define', '상품'): 4530}

In [49]:
from multisage.builder import PandasGraphBuilder
import torch

def graph_maker(df):
    attributes_df, attributes, attributes_merged_df = seperateDF(df, '특징')
    ingredient_df, ingredients, ingredient_merged_df = seperateDF(df,'성분')
    
    graph_builder = PandasGraphBuilder()
    graph_builder.add_entities(attributes, '특징_id', '특징')
    graph_builder.add_entities(df, 'ID', '상품')
    graph_builder.add_binary_relations(attributes_merged_df, '특징_id', 'ID', 'define')
    graph_builder.add_binary_relations(attributes_merged_df, 'ID', '특징_id', 'define-by')
    g = graph_builder.build()
    
    df['성분'] = df['성분'].fillna('[]')
    df['평점'] = df['평점'].fillna(0.0)
    
    g.nodes['특징'].data['id'] = torch.LongTensor(attributes['특징_id'].cat.codes.values)

    attribute_columns = attributes_df.columns.drop(['ID', '상품명', '상품 카테고리 대분류', '상품 카테고리 중분류','상품 카테고리 소분류','제조사','브랜드','특징','느낌','평점','성분'])
    attributes_df[attribute_columns] = attributes_df[attribute_columns].fillna(False).astype('bool')
    g.nodes['상품'].data['특징'] = torch.FloatTensor(attributes_df[attribute_columns].values)

    attribute_columns = ingredient_df.columns.drop(['ID', '상품명', '상품 카테고리 대분류', '상품 카테고리 중분류','상품 카테고리 소분류','제조사','브랜드','특징'])
    ingredient_df[attribute_columns] = ingredient_df[attribute_columns].fillna(False).astype('bool')
    g.nodes['상품'].data['성분'] = torch.FloatTensor(ingredient_df[attribute_columns].values)
    
    g.edges['define'].data['rating'] = torch.LongTensor(df['평점'].values)
    g.edges['define-by'].data['rating'] = torch.LongTensor(df['평점'].values)
    
    # 그래프 구조 확인

    print("Number of nodes per type:")
    print(g.number_of_nodes())
    print("Number of edges per type:")
    print(g.number_of_edges())
    print("Node types:")
    print(g.ntypes)
    print("Edge types:")
    print(g.etypes)

    # 노드 데이터 확인
    for ntype in g.ntypes:
        print(f"Node type: {ntype}")
        print(g.nodes[ntype].data)

    # 엣지 데이터 확인
    for stype, etype, dtype in g.canonical_etypes:
        print(f"Edge type: {etype}")
        print(g.edges[etype].data)

    # 그래프 구조 확인
    print("Graph structure:")
    print(g)
    
    return g

In [50]:
g = graph_maker(df)

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

...

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_copy[i] = data_list
C:\Users\kimhw\AppData\Local\Temp\ipykernel_22304\90207233.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.conca

Number of nodes per type:
8057
Number of edges per type:
9060
Node types:
['상품', '특징']
Edge types:
['define-by', 'define']
Node type: 상품
{'특징': tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [0., 1., 0.,  ..., 0., 0., 0.],
        [0., 0., 1.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 1., 0.],
        [0., 0., 0.,  ..., 0., 0., 1.],
        [0., 0., 0.,  ..., 0., 0., 0.]]), '성분': tensor([[1., 1., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 1., 1.,  ..., 0., 0., 0.],
        ...,
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 0.],
        [1., 0., 1.,  ..., 0., 0., 1.]])}
Node type: 특징
{'id': tensor([   0,    1,    2,  ..., 3524, 3525, 3526])}
Edge type: define-by
{'rating': tensor([4, 0, 4,  ..., 0, 0, 0])}
Edge type: define
{'rating': tensor([4, 0, 4,  ..., 0, 0, 0])}
Graph structure:
Graph(num_nodes={'상품': 4530, '특징': 3527},
      num_edges={('상품', 'define-by', '특징'): 4530, ('특징', 'define', '상품'): 4530}

In [48]:
import dgl
import pickle

output_path = 'dataset/Haircare/haircare_graph.dgl'
dgl.save_graphs(output_path, [g])

dataset = {
    'train-graph': g,
    'context-type': '특징',
    'item-type': '상품',
    'context-to-item-type': 'define',
    'item-to-context-type': 'define-by'}

with open('dataset/Haircare/haircare_data.pickle', 'wb') as f:
    pickle.dump(dataset, f)

# Normal Query

In [52]:
from scipy import spatial
import numpy as np
import pandas as pd

g = dgl.load_graphs('./dataset/Haircare/haircare_graph.dgl')[0][0]

saved_npz = np.load('./multisage/' + 'h_items.npz')
h_item = saved_npz['movie_vectors']
tree = spatial.KDTree(h_item.tolist())

In [53]:
df

ID                          상품명 상품 카테고리 대분류 상품 카테고리 중분류  \
0     28269744554  검은콩 보습 진정 모닝 샴푸 로즈마리향 400ml      화장품/미용        헤어케어   
1     29502248618            어글리솝 더 님 민감성용 97g      화장품/미용        헤어케어   
2     25261181522            가려운 두피케어 샴푸 850ml      화장품/미용        헤어케어   
3     33208679619            쿨 멘솔 샴푸 850ml(신형)      화장품/미용        헤어케어   
4      4053407990              카페인 샴푸 C1 250ml      화장품/미용        헤어케어   
...           ...                          ...         ...         ...   
4525  32238886623              니욕 샴푸바 그린터치 80g      화장품/미용        헤어케어   
4526  32241470618                일랑일랑 헤어바 100g      화장품/미용        헤어케어   
4527  36623871618                캐럿히어로 샴푸바 50g      화장품/미용        헤어케어   
4528  32240713619         촌스러운 샴푸바 두피 튼튼 청 80g      화장품/미용        헤어케어   
4529  36843821623              리커버 테라피 샴푸바 80g      화장품/미용        헤어케어   

     상품 카테고리 소분류     제조사    브랜드  \
0             샴푸  동방코스메틱     올솔   
1             샴푸   프롬더랜드  프롬더랜드   
2             샴푸     P&G  헤드앤숄더   
3             샴푸     P&G  헤드앤숄더   
4             샴푸    닥터볼프    알페신   
...          ...     ...    ...   
4525          샴푸     NaN    NaN   
4526          샴푸     NaN    NaN   
4527          샴푸     NaN     맨심   
4528          샴푸     NaN  스페이스선   
4529          샴푸     NaN  그로우어스   

                                                     특징  \
0     ['샴푸', '모든두피용', '모든 모발용', '일반샴푸', '펌프형', '머릿결개...   
1     ['샴푸', '일반샴푸', '머릿결개선', '세정력', '풍부한 거품', '저자극'...   
2           ['샴푸', '일반샴푸', '펌프형', '세정력', '비듬케어', '그린향']   
3     ['샴푸', '일반샴푸', '펌프형', '세정력', '풍부한 거품', '유분제거',...   
4                         ['샴푸', '일반샴푸', '리퀴드형', '기타향']   
...                                                 ...   
4525  ['샴푸', '샴푸바', '고체형', '머릿결개선', '세정력', '풍부한 거품',...   
4526  ['샴푸', '샴푸바', '고체형', '세정력', '풍부한 거품', '상쾌함', '...   
4527                                      ['샴푸', '샴푸바']   
4528  ['샴푸', '샴푸바', '세정력', '풍부한 거품', '상쾌함', '저자극', '...   
4529                               ['샴푸', '샴푸바', '세정력']   

                                             느낌   평점  \
0                                      ['성분좋은']  4.8   
1                                          ['']  0.0   
2                     ['가려운두피', '두피가시원한', '비듬']  4.8   
3                                          ['']  4.8   
4     ['두피가시원한', '쿨링감있는', '탈모', '향좋은', '힘없는모발']  4.8   
...                                         ...  ...   
4525                                       ['']  0.0   
4526                                       ['']  0.0   
4527                                       ['']  0.0   
4528                                       ['']  0.0   
4529                                       ['']  0.0   

                                                     성분  
0     [검정콩추출물, 다이소듐라우레스설포석시네이트, 정제수, 라우릴베타인, 프로필렌글라이...  
1                                                    []  
2     [정제수, 소듐라우레스설페이트, 소듐자일렌설포네이트, 글라이콜다이스테아레이트, 코카...  
3                                                    []  
4     [리모넨, 멘톨, 비타민E, 판테놀, 시트릭애씨드, 소듐벤조에이트, 프로필파라벤, ...  
...                                                 ...  
4525                                                 []  
4526                                                 []  
4527                                                 []  
4528                                                 []  
4529  [소듐코코일이세티오네이트, 옥수수전분, 정제수, 글리세린, 해바라기씨오일, 잔탄검,...  

[4530 rows x 11 columns]

In [54]:
entities = df['ID'].astype('category')
m_entities = entities.cat.reorder_categories(df['ID'].values)

index_id_to_ID = {}
ID_to_index_id = {}
for idx, ID in enumerate(m_entities):
    index_id_to_ID[idx] = ID
    ID_to_index_id[ID] = idx
    
h_query = h_item[ID_to_index_id[25261181522]]
index_ids = tree.query(h_query, 10)[1]
IDs = [index_id_to_ID[idx] for idx in index_ids]

for mid in IDs:
    print(df[df['ID']==mid]['상품명'].values)

['가려운 두피케어 샴푸 850ml']
['가려운 두피 케어 샴푸 550ml(신형)']
['가려운 두피케어 샴푸 1130ml']
['울트라 쿨 멘솔 샴푸 1200ml']
['두피 토탈 솔루션 샴푸 시트러스 레몬 750ml']
['딥 클린 샴푸 1200ml']
['소루쟁이 샴푸 300ml']
['딥 클린 샴푸 850ml(신형)']
['애플 프레쉬 샴푸 850ml(신형)']
['클라리파잉 샴푸 1000ml']


# context Query

In [56]:
import sys

sys.path.append('C:/Users/kimhw/Desktop/데이터 청년 캠퍼스/Github/ESG-Recommender-System-by-MultiSAGE/multisage')
from model import MultiSAGEModel
from sampler import ItemToItemBatchSampler, NeighborSampler, PinSAGECollator

load_dict = torch.load('./multisage/MultiSAGE_weights.pth')

model = MultiSAGEModel(g, '상품', '특징', 512, 2, 3)
model.load_state_dict(load_dict)

batch_sampler = ItemToItemBatchSampler(g, '특징', '상품', 512)
neighbor_sampler = NeighborSampler(
    g, '특징', '상품', 2, 0.5, 10, 5, 2)
collator = PinSAGECollator(neighbor_sampler, g, '상품', '특징')

In [60]:
index_id = ID_to_index_id[25261181522]
with torch.no_grad():
    blocks, context_blocks = collator.collate_point(index_id=index_id)
    context_batch = model.get_representation(blocks, context_blocks, context_id=86)
    
tree.query(context_batch.numpy()[0], 10)

index_ids = tree.query(context_batch.numpy()[0], 10)[1]
IDs = [index_id_to_ID[idx] for idx in index_ids]
for mid in IDs:
    print(df[df['ID']==mid]['상품명'].values)

2
tensor([2])
execute context query
['가려운 두피케어 샴푸 850ml']
['가려운 두피 케어 샴푸 550ml(신형)']
['가려운 두피케어 샴푸 1130ml']
['울트라 쿨 멘솔 샴푸 1200ml']
['두피 토탈 솔루션 샴푸 시트러스 레몬 750ml']
['딥 클린 샴푸 1200ml']
['딥 클린 샴푸 850ml(신형)']
['애플 프레쉬 샴푸 850ml(신형)']
['소루쟁이 샴푸 300ml']
['애플 프레쉬 샴푸 300ml']
